In [1]:
import requests
import json
import xlrd
import xlwt
from datetime import datetime
import time
# 变量定义
login_url = "http://10.200.32.39/jingbo-api/api/server/login"
search_url = "http://10.200.32.39/jingbo-api/api/warehouse/dwDataItem/queryByItemNos"

login_push_url = "http://10.200.32.39/jingbo-api/api/server/login"
upload_url = "http://10.200.32.39/jingbo-api/api/dw/dataValue/pushDataValueList"

login_data = {
    "data": {
        "account": "api_dev",
        "password": "ZTEwYWRjMzk0OWJhNTlhYmJlNTZlMDU3ZjIwZjg4M2U=",
        "tenantHashCode": "8a4577dbd919675758d57999a1e891fe",
        "terminal": "API"
    },
    "funcModule": "API",
    "funcOperation": "获取token"
}

login_push_data = {
    "data": {
        "account": "api_dev",
        "password": "ZTEwYWRjMzk0OWJhNTlhYmJlNTZlMDU3ZjIwZjg4M2U=",
        "tenantHashCode": "8a4577dbd919675758d57999a1e891fe",
        "terminal": "API"
    },
    "funcModule": "API",
    "funcOperation": "获取token"
}

read_file_path_name = "沥青数据项.xls"
one_cols = []
two_cols = []

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sn
import random
import time




from plotly import __version__
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

from sklearn import preprocessing

from pandas import Series,DataFrame

import matplotlib.pyplot as plt

import sklearn.datasets as datasets

#导入机器学习算法模型
from sklearn.linear_model import Lasso
from xgboost import XGBRegressor

import datetime
import statsmodels.api as sm
# from keras.preprocessing.sequence import TimeseriesGenerator
from tensorflow.keras.preprocessing.sequence import TimeseriesGenerator

import plotly.express as px
import plotly.graph_objects as go

import xgboost as xgb
from xgboost import plot_importance, plot_tree
from sklearn.metrics import mean_absolute_error
from statsmodels.tools.eval_measures import mse,rmse
from sklearn.model_selection import GridSearchCV
from xgboost import XGBRegressor
import warnings
import pickle

from sklearn.metrics import mean_squared_error

#切割训练数据和样本数据
from sklearn.model_selection import train_test_split

#用于模型评分
from sklearn.metrics import r2_score

le = preprocessing.LabelEncoder()

# print(__version__) # requires version >= 1.9.0


import cufflinks as cf
cf.go_offline()

random.seed(100)

%matplotlib inline

# 数据获取

def get_head_auth():
    login_res = requests.post(url=login_url, json=login_data, timeout=(3, 5))
    text = json.loads(login_res.text)
    if text["status"]:
        token = text["data"]["accessToken"]
        return token
    else:
        print("获取认证失败")
        return None


def get_data_value(token, dataItemNoList,date=''):

    search_data = {
        "data": {
            "date": get_cur_time(date)[0],
            "dataItemNoList": dataItemNoList
        },
        "funcModule": "数据项",
        "funcOperation": "查询"
    }
    headers = {"Authorization": token}
    search_res = requests.post(url=search_url, headers=headers, json=search_data, timeout=(3, 5))
    search_value = json.loads(search_res.text)["data"]
    if search_value:
        return search_value
    else:
        print("今天没有新数据")
        return None


# xls文件处理





def write_xls(data,date):
    # 创建一个Workbook对象
    workbook = xlwt.Workbook()

    # 创建一个Sheet对象，可指定名称
    sheet = workbook.load('Sheet1')

    # 写入数据行
    for row_index, row_data in enumerate(data):
        for col_index, cell_data in enumerate(row_data):
            sheet.write(row_index, col_index, cell_data)

    # 保存Workbook到文件
    workbook.save(get_cur_time(date)[0] + '.xls')


def get_cur_time(date = ''):
    if date == '':
        import datetime
        now = datetime.datetime.now()
    else:
        now = date
    year = now.year
    month = now.month
    day = now.day

    if month < 10:
        month = "0" + str(month)
    if day < 10:
        day = "0" + str(day)
    cur_time = str(year) + str(month) + str(day)
    cur_time2 = str(year) + "-" + str(month) + "-" + str(day)
#     cur_time = '20231007'
#     cur_time2 = '2023-10-07'
    return cur_time, cur_time2


def get_head_push_auth():
    login_res = requests.post(url=login_push_url, json=login_push_data, timeout=(3, 5))
    text = json.loads(login_res.text)
    if text["status"]:
        token = text["data"]["accessToken"]
        return token
    else:
        print("获取认证失败")
        return None



def upload_data_to_system(token_push,date):
    data = {
        "funcModule": "数据表信息列表",
        "funcOperation": "新增",
        "data": [
            {"dataItemNo": "C01100036|Forecast_Price|ACN",
             "dataDate": get_cur_time(date)[0],
             "dataStatus": "add",
             "dataValue": forecast_price()
             }

        ]
    }
    headers = {"Authorization": token_push}
    res = requests.post(url=upload_url, headers=headers, json=data, timeout=(3, 5))
    print(res.text)

    
# def upload_data_to_system(token):
#     data = {
#         "funcModule": "数据表信息列表",
#         "funcOperation": "新增",
#         "data": [
#             {"dataItemNo": "C01100036|Forecast_ Price|ACN",
#              "dataDate": '20230706',
#              "dataStatus": "add",
#              "dataValue": 3780.0
#              }

#         ]
#     }
#     headers = {"Authorization": token}
#     res = requests.post(url=upload_url, headers=headers, json=data, timeout=(3, 5))
#     print(res.text)

def forecast_price():
    df_test = pd.read_excel('沥青数据项.xls',sheet_name='数据项历史数据')
    df_test.drop([0],inplace=True)
    df_test[['汽油执行价','柴油执行价','齐鲁石化销量','齐鲁石化产量','齐鲁石化成交价','齐鲁石化库存','科力达销量',
            '科力达产量','科力达成交价','科力达库存','弘润销量','弘润产量','弘润成交价','弘润库存','市场成交价','京博指导价',
            '布伦特上周收盘价','布伦特昨日收盘价','布伦特收盘价','上期所沥青主力合约','隆重资讯沥青日开工率','隆重资讯沥青月库存',
            '隆重资讯沥青月产量','隆重资讯沥青表观消费量','隆重资讯社会库存率','厂区库容','京博提货量','即期成本','异地库库存',
            '京博签单量','京博库存量','京博产量','加权平均成交价']] = df_test[['汽油执行价','柴油执行价','齐鲁石化销量',
            '齐鲁石化产量','齐鲁石化成交价','齐鲁石化库存','科力达销量',
            '科力达产量','科力达成交价','科力达库存','弘润销量','弘润产量','弘润成交价','弘润库存','市场成交价','京博指导价',
            '布伦特上周收盘价','布伦特昨日收盘价','布伦特收盘价','上期所沥青主力合约','隆重资讯沥青日开工率','隆重资讯沥青月库存',
            '隆重资讯沥青月产量','隆重资讯沥青表观消费量','隆重资讯社会库存率','厂区库容','京博提货量','即期成本','异地库库存',
            '京博签单量','京博库存量','京博产量','加权平均成交价']].astype('float')
    # df_test['日期']=pd.to_datetime(df_test['日期'],  format='%d/%m/%Y',infer_datetime_format=True)
    df_test['日期']=pd.to_datetime(df_test['日期'],  format='%Y-%m-%d',infer_datetime_format=True)

    #查看每个特征缺失值数量
    MisVal_Check=df_test.isnull().sum().sort_values(ascending=False)
    #去掉缺失值百分比>0.4的特征，去掉这些特征后的新表格命名为df_test_1
    df_MisVal_Check = pd.DataFrame(MisVal_Check,)#
    df_MisVal_Check_1=df_MisVal_Check.reset_index()
    df_MisVal_Check_1.columns=['Variable_Name','Missing_Number'] 
    df_MisVal_Check_1['Missing_Number']=df_MisVal_Check_1['Missing_Number']/len(df_test)
    df_test_1=df_test.drop(df_MisVal_Check_1[df_MisVal_Check_1['Missing_Number']>0.4].Variable_Name,axis = 1)

    #将缺失值补为前一个或者后一个数值
    df_test_1=df_test_1.fillna(df_test.ffill())
    df_test_1=df_test_1.fillna(df_test_1.bfill())

    # 选择用于模型训练的列名称
    col_for_training = df_test_1.columns
    import joblib
    Best_model_DalyLGPrice = joblib.load("日度价格预测_最佳模型.pkl")
    # 最新的一天为最后一行的数据
    df_test_1_Day = df_test_1.tail(1)
    # 移除不需要的列
    df_test_1_Day.index = df_test_1_Day["日期"]
    df_test_1_Day = df_test_1_Day.drop(["日期"], axis= 1)
    df_test_1_Day=df_test_1_Day.drop('京博指导价',axis=1)
    df_test_1_Day=df_test_1_Day.dropna()

    # df_test_1_Day
    #预测今日价格，显示至小数点后两位
    Ypredict_Today=Best_model_DalyLGPrice.predict(df_test_1_Day)

    df_test_1_Day['日度预测价格']=Ypredict_Today
    print(df_test_1_Day['日度预测价格'])
    a = df_test_1_Day['日度预测价格']
    a = a[0]
    a = float(a)
    a = round(a,2)
    return a
def optimize_Model():
    from sklearn.model_selection import train_test_split
    from sklearn.impute  import SimpleImputer
    from sklearn.preprocessing import OrdinalEncoder
    from sklearn.feature_selection import SelectFromModel
    from sklearn.metrics import mean_squared_error, r2_score

    pd.set_option('display.max_rows',40)  
    pd.set_option('display.max_columns',40)  
    df_test = pd.read_excel('沥青数据项.xls',sheet_name='数据项历史数据')
    df_test.drop([0],inplace=True)
    df_test[['汽油执行价','柴油执行价','齐鲁石化销量','齐鲁石化产量','齐鲁石化成交价','齐鲁石化库存','科力达销量',
            '科力达产量','科力达成交价','科力达库存','弘润销量','弘润产量','弘润成交价','弘润库存','市场成交价','京博指导价',
            '布伦特上周收盘价','布伦特昨日收盘价','布伦特收盘价','上期所沥青主力合约','隆重资讯沥青日开工率','隆重资讯沥青月库存',
            '隆重资讯沥青月产量','隆重资讯沥青表观消费量','隆重资讯社会库存率','厂区库容','京博提货量','即期成本','异地库库存',
            '京博签单量','京博库存量','京博产量','加权平均成交价']] = df_test[['汽油执行价','柴油执行价','齐鲁石化销量','齐鲁石化产量','齐鲁石化成交价','齐鲁石化库存','科力达销量',
            '科力达产量','科力达成交价','科力达库存','弘润销量','弘润产量','弘润成交价','弘润库存','市场成交价','京博指导价',
            '布伦特上周收盘价','布伦特昨日收盘价','布伦特收盘价','上期所沥青主力合约','隆重资讯沥青日开工率','隆重资讯沥青月库存',
            '隆重资讯沥青月产量','隆重资讯沥青表观消费量','隆重资讯社会库存率','厂区库容','京博提货量','即期成本','异地库库存',
            '京博签单量','京博库存量','京博产量','加权平均成交价']].astype('float')
    # df_test = pd.read_csv('定价模型数据收集20190901-20230615.csv',encoding = 'gbk',engine = 'python')
    # df_test['日期']=pd.to_datetime(df_test['日期'],  format='%m/%d/%Y',infer_datetime_format=True)
    df_test['日期']=pd.to_datetime(df_test['日期'],  format='%Y-%m-%d',infer_datetime_format=True)
    # df_test.tail(3)
    MisVal_Check=df_test.isnull().sum().sort_values(ascending=False)
    #去掉缺失值百分比>0.4的特征，去掉这些特征后的新表格命名为df_test_1
    df_MisVal_Check = pd.DataFrame(MisVal_Check,)#
    df_MisVal_Check_1=df_MisVal_Check.reset_index()
    df_MisVal_Check_1.columns=['Variable_Name','Missing_Number'] 
    df_MisVal_Check_1['Missing_Number']=df_MisVal_Check_1['Missing_Number']/len(df_test)
    df_test_1=df_test.drop(df_MisVal_Check_1[df_MisVal_Check_1['Missing_Number']>0.4].Variable_Name,axis = 1)
    #将缺失值补为前一个或者后一个数值
    df_test_1=df_test_1.fillna(df_test.ffill())
    df_test_1=df_test_1.fillna(df_test_1.bfill())
    df_test_1["日期"] = pd.to_datetime(df_test_1["日期"])
    df_test_1.index = df_test_1["日期"]
    df_test_1 = df_test_1.drop(["日期"], axis= 1)
    dataset1=df_test_1.drop('京博指导价',axis=1)#.astype(float)

    y=df_test_1['京博指导价']

    x=dataset1 

    train = x
    target = y

    #切割数据样本集合测试集
    X_train,x_test,y_train,y_true = train_test_split(train,target,test_size=0.2,random_state=0)
    
    
    from sklearn.linear_model import Lasso
    from xgboost import XGBRegressor

    from datetime import datetime
    import statsmodels.api as sm
    # from keras.preprocessing.sequence import TimeseriesGenerator
    from tensorflow.keras.preprocessing.sequence import TimeseriesGenerator

    import plotly.express as px
    import plotly.graph_objects as go

    import xgboost as xgb
    from xgboost import plot_importance, plot_tree
    from sklearn.metrics import mean_absolute_error
    from statsmodels.tools.eval_measures import mse,rmse
    from sklearn.model_selection import GridSearchCV
    from xgboost import XGBRegressor
    import warnings
    import pickle

    from sklearn.metrics import mean_squared_error

    #切割训练数据和样本数据
    from sklearn.model_selection import train_test_split

    #用于模型评分
    from sklearn.metrics import r2_score

    #模型缩写
    Lasso =  Lasso(random_state=0)
    XGBR = XGBRegressor(random_state=0)
    Lasso.fit(X_train,y_train)
    XGBR.fit(X_train,y_train)
    y_pre_Lasso = Lasso.predict(x_test)
    y_pre_XGBR = XGBR.predict(x_test)

    #计算Lasso、XGBR、RandomForestR、AdaBoostR、GradientBoostingR、BaggingRegressor各模型的R²
    Lasso_score = r2_score(y_true,y_pre_Lasso)
    XGBR_score=r2_score(y_true,y_pre_XGBR)

    #计算Lasso、XGBR的MSE和RMSE
    Lasso_MSE=mean_squared_error(y_true, y_pre_Lasso)
    XGBR_MSE=mean_squared_error(y_true, y_pre_XGBR)

    Lasso_RMSE=np.sqrt(Lasso_MSE)
    XGBR_RMSE=np.sqrt(XGBR_MSE)
    model_results = pd.DataFrame([['Lasso', Lasso_RMSE, Lasso_score],
                                 ['XgBoost', XGBR_RMSE, XGBR_score]],
                   columns = ['模型(Model)','均方根误差(RMSE)', 'R^2 score'])
    model_results1=model_results.set_index('模型(Model)')

    model_results1
    def plot_feature_importance(importance,names,model_type):
        feature_importance = np.array(importance)
        feature_names = np.array(names)

        data={'feature_names':feature_names,'feature_importance':feature_importance}
        fi_df = pd.DataFrame(data)

        fi_df.sort_values(by=['feature_importance'], ascending=False,inplace=True)

        plt.figure(figsize=(10,8))
        sn.barplot(x=fi_df['feature_importance'], y=fi_df['feature_names'])

        plt.title(model_type + " "+'FEATURE IMPORTANCE')
        plt.xlabel('FEATURE IMPORTANCE')
        plt.ylabel('FEATURE NAMES')
        from pylab import mpl
    %pylab
    mpl.rcParams['font.sans-serif'] = ['SimHei']
    from xgboost import XGBRegressor
    from sklearn.model_selection import GridSearchCV

    estimator = XGBRegressor(random_state=0,
        nthread=4,
        seed=0
    )
    parameters = {
        'max_depth': range (2, 11, 2),     # 树的最大深度
        'n_estimators': range (50, 101, 10),  # 迭代次数
        'learning_rate': [0.01, 0.03, 0.1, 0.3, 0.5, 1]
    }

    grid_search_XGB = GridSearchCV(
        estimator=estimator,
        param_grid=parameters,
    #     n_jobs = 10,
        cv = 3,
        verbose=True
    )

    grid_search_XGB.fit(X_train, y_train)
    print("Best score: %0.3f" % grid_search_XGB.best_score_)
    print("Best parameters set:")
    best_parameters = grid_search_XGB.best_estimator_.get_params()
    for param_name in sorted(parameters.keys()):
        print("\t%s: %r" % (param_name, best_parameters[param_name]))
    y_pred = grid_search_XGB.predict(x_test)

    op_XGBR_score = r2_score(y_true,y_pred)
    op_XGBR_MSE= mean_squared_error(y_true, y_pred)
    op_XGBR_RMSE= np.sqrt(op_XGBR_MSE)

    model_results2 = pd.DataFrame([['Optimized_Xgboost', op_XGBR_RMSE, op_XGBR_score]],
                   columns = ['模型(Model)', '均方根误差(RMSE)', 'R^2 score'])
    model_results2=model_results2.set_index('模型(Model)')

    # results = model_results1.append(model_results2, ignore_index = False)
    results = pd.concat([model_results1,model_results2],ignore_index=True)
    results
    import pickle

    Pkl_Filename = "日度价格预测_最佳模型.pkl"  

    with open(Pkl_Filename, 'wb') as file:  
       pickle.dump(grid_search_XGB, file)




    


   

def read_xls_data():
    global one_cols, two_cols
    # 打开 XLS 文件
    workbook = xlrd.open_workbook(read_file_path_name)

    # 获取所有表格名称
    # sheet_names = workbook.sheet_names()

    # 选择第一个表格
    sheet = workbook.sheet_by_index(0)

    # 获取行数和列数
    num_rows = sheet.nrows
    # num_cols = sheet.ncols

    # 遍历每一行，获取单元格数据
    # for i in range(num_rows):
    #     row_data = sheet.row_values(i)
    #     one_cols.append(row_data)
    #     two_cols.append(row_data[1])

    row_data = sheet.row_values(1)
    one_cols = row_data

    # 关闭 XLS 文件
    # workbook.close()




def start():
    '''预测上传数据'''
    read_xls_data()

    token = get_head_auth()
    if not token:
        return
    token_push = get_head_push_auth()
    if not token_push:
        return

    datas = get_data_value(token, one_cols[1:])
    if not datas:
        return

    # data_list = [two_cols, one_cols]
    append_rows = [get_cur_time()[1]]
    dataItemNo_dataValue = {}
    for data_value in datas:
        if "dataValue" not in data_value:
            print(data_value)
            dataItemNo_dataValue[data_value["dataItemNo"]] = ""
        else:
            dataItemNo_dataValue[data_value["dataItemNo"]] = data_value["dataValue"]
       
    for value in one_cols[1:]:
        if value in dataItemNo_dataValue:
            append_rows.append(dataItemNo_dataValue[value])
        else:
            append_rows.append("")
    save_xls(append_rows)
    optimize_Model()
    upload_data_to_system(token_push)
    # data_list.append(three_cols)
    # write_xls(data_list)


def start_3(date):
    '''预测上传数据'''
    read_xls_data()

    token = get_head_auth()
    if not token:
        return
    token_push = get_head_push_auth()
    if not token_push:
        return

    datas = get_data_value(token, one_cols[1:],date)
    if not datas:
        return

    # data_list = [two_cols, one_cols]
    append_rows = [get_cur_time(date)[1]]
    dataItemNo_dataValue = {}
    for data_value in datas:
        if "dataValue" not in data_value:
            print(data_value)
            dataItemNo_dataValue[data_value["dataItemNo"]] = ""
        else:
            dataItemNo_dataValue[data_value["dataItemNo"]] = data_value["dataValue"]
       
    for value in one_cols[1:]:
        if value in dataItemNo_dataValue:
            append_rows.append(dataItemNo_dataValue[value])
        else:
            append_rows.append("")
    save_xls(append_rows)
    optimize_Model()
    upload_data_to_system(token_push,date)
    # data_list.append(three_cols)
    # write_xls(data_list)



def start_1():
    '''更新数据'''
    read_xls_data()

    token = get_head_auth()
    if not token:
        return
    

    datas = get_data_value(token, one_cols[1:])
    if not datas:
        return

    # data_list = [two_cols, one_cols]
    append_rows = [get_cur_time()[1]]
    dataItemNo_dataValue = {}
    for data_value in datas:
        if "dataValue" not in data_value:
            print(data_value)
            dataItemNo_dataValue[data_value["dataItemNo"]] = ""
        else:
            dataItemNo_dataValue[data_value["dataItemNo"]] = data_value["dataValue"]
       
    for value in one_cols[1:]:
        if value in dataItemNo_dataValue:
            append_rows.append(dataItemNo_dataValue[value])
        else:
            append_rows.append("")
    save_xls_1(append_rows)

    
    # data_list.append(three_cols)
    # write_xls(data_list)


def start_2(date):
    '''更新数据'''
    read_xls_data()

    token = get_head_auth()
    if not token:
        return
    

    datas = get_data_value(token, one_cols[1:],date)
    if not datas:
        return

    # data_list = [two_cols, one_cols]
    append_rows = [get_cur_time(date=date)[1]]
    dataItemNo_dataValue = {}
    for data_value in datas:
        if "dataValue" not in data_value:
            print(data_value)
            dataItemNo_dataValue[data_value["dataItemNo"]] = ""
        else:
            dataItemNo_dataValue[data_value["dataItemNo"]] = data_value["dataValue"]
       
    for value in one_cols[1:]:
        if value in dataItemNo_dataValue:
            append_rows.append(dataItemNo_dataValue[value])
        else:
            append_rows.append("")
    print('新增数据：',append_rows)
    save_xls_1(append_rows)

    
    # data_list.append(three_cols)
    # write_xls(data_list)
    
def save_xls_1(append_rows):

    # 打开xls文件
    workbook = xlrd.open_workbook('沥青数据项.xls')

    # 获取所有sheet的个数
    sheet_count = len(workbook.sheet_names())

    # 获取所有sheet的名称
    sheet_names = workbook.sheet_names()

    new_workbook = xlwt.Workbook()
    for i in range(sheet_count):
        # 获取当前sheet
        sheet = workbook.sheet_by_index(i)

        # 获取sheet的行数和列数
        row_count = sheet.nrows - 1
        col_count = sheet.ncols
        # 获取原有数据
        data = []
        for row in range(row_count):
            row_data = []
            for col in range(col_count):
                row_data.append(sheet.cell_value(row, col))
            data.append(row_data)
        # 创建xlwt的Workbook对象
        # 创建sheet
        new_sheet = new_workbook.add_sheet(sheet_names[i])

        # 将原有的数据写入新的sheet
        for row in range(row_count):
            for col in range(col_count):
                new_sheet.write(row, col, data[row][col])

        if i == 0:
            # 在新的sheet中添加数据
            for col in range(col_count):
                new_sheet.write(row_count, col, append_rows[col])

    # 保存新的xls文件
    new_workbook.save("沥青数据项.xls")    

    
    
    
def check_data(dataItemNo):
    token = get_head_auth()
    if not token:
        return

    datas = get_data_value(token, dataItemNo)
    if not datas:
        return


def save_xls(append_rows):

    # 打开xls文件
    workbook = xlrd.open_workbook('沥青数据项.xls')

    # 获取所有sheet的个数
    sheet_count = len(workbook.sheet_names())

    # 获取所有sheet的名称
    sheet_names = workbook.sheet_names()

    new_workbook = xlwt.Workbook()
    for i in range(sheet_count):
        # 获取当前sheet
        sheet = workbook.sheet_by_index(i)

        # 获取sheet的行数和列数
        row_count = sheet.nrows
        col_count = sheet.ncols
        # 获取原有数据
        data = []
        for row in range(row_count):
            row_data = []
            for col in range(col_count):
                row_data.append(sheet.cell_value(row, col))
            data.append(row_data)
        # 创建xlwt的Workbook对象
        # 创建sheet
        new_sheet = new_workbook.add_sheet(sheet_names[i])

        # 将原有的数据写入新的sheet
        for row in range(row_count):
            for col in range(col_count):
                new_sheet.write(row, col, data[row][col])

        if i == 0:
            # 在新的sheet中添加数据
            for col in range(col_count):
                new_sheet.write(row_count, col, append_rows[col])

    # 保存新的xls文件
    new_workbook.save("沥青数据项.xls")


if __name__ == "__main__":
    pass
    # 需要单独运行放开
#      start()

    # 每天定时12点运行
    # while True:
    #     # 获取当前时间
    #     current_time = time.strftime("%H:%M:%S", time.localtime())
    #     current_time_1 = time.strftime("%H:%M:%S", time.localtime())

    #     # 判断当前时间是否为执行任务的时间点
    #     if current_time == "12:00:00":
    #         print("执行定时任务")
    #         start()

    #     # 休眠1秒钟，避免过多占用CPU资源
    #         time.sleep(1)
        
    #     elif current_time_1 == "20:00:00":
    #         print("更新数据")
    #         start_1()
    #     time.sleep(1)


#     # 检测数据准确性, 需要检测放开
#     # check_data("100028098|LISTING_PRICE")
#     # check_data("9137070016544622XB|DAY_Yield")


In [3]:
from datetime import datetime, timedelta

start_date = datetime(2024, 10, 31)
end_date = datetime(2024, 12, 1)

while start_date < end_date:
    print(start_date.strftime('%Y%m%d'))
    start_3(start_date)
    time.sleep(1)
    start_2(start_date)
    start_date += timedelta(days=1)

20241031


C:\Users\EDY\AppData\Local\Temp\ipykernel_3076\2242856620.py:299: UserWarning:

The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.



Using matplotlib backend: <object object at 0x000001EAB4F2F0A0>
%pylab is deprecated, use %matplotlib inline and import the required libraries.
Populating the interactive namespace from numpy and matplotlib
Fitting 3 folds for each of 180 candidates, totalling 540 fits


d:\ProgramData\anaconda3\Lib\site-packages\IPython\core\magics\pylab.py:162: UserWarning:

pylab import has clobbered these variables: ['datetime', 'plot', '__version__', 'random']
`%matplotlib` prevents importing * from pylab and numpy



Best score: 0.997
Best parameters set:
	learning_rate: 0.1
	max_depth: 6
	n_estimators: 100


...

Using matplotlib backend: QtAgg
%pylab is deprecated, use %matplotlib inline and import the required libraries.
Populating the interactive namespace from numpy and matplotlib
Fitting 3 folds for each of 180 candidates, totalling 540 fits
Best score: 0.997
Best parameters set:
	learning_rate: 0.1
	max_depth: 8
	n_estimators: 100


C:\Users\EDY\AppData\Local\Temp\ipykernel_3076\2242856620.py:239: UserWarning:

The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.



日期
2024-11-30    3503.998047
Name: 日度预测价格, dtype: float32


C:\Users\EDY\AppData\Local\Temp\ipykernel_3076\2242856620.py:273: FutureWarning:

Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`



{"confirmFlg":false,"status":true}
新增数据： ['2024-11-30', 7576.0, 6957.0, '', '', '', '', '', '', '', '', '', '', '', '', '', 3530.0, 74.73, 71.45, '', '', '', 61.8, '', '', '', 229522.1, 6820.44, 3166.3388, '', 1.0, 76240.6094746, 6410.4865, 3480.56]
